# Imports

In [11]:
#!pip install catboost

In [1]:
import pandas as pd
import numpy as np

from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import RobustScaler, StandardScaler
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.metrics import mean_squared_error
import catboost as cb

# Read diamonds

In [2]:
diamonds_train_sorted = pd.read_csv('../data/diamonds_train_sorted.csv')
diamonds_train_sorted.head()

price  carat  cut  color  clarity  depth  table     x     y     z
0    326   0.21    4      1        2   59.8   61.0  3.89  3.84  2.31
1    326   0.23    0      1        1   61.5   55.0  3.95  3.98  2.43
2    327   0.23    1      1        4   56.9   65.0  4.05  4.07  2.31
3    334   0.29    4      5        3   62.4   58.0  4.20  4.23  2.63
4    335   0.31    1      6        1   63.3   58.0  4.34  4.35  2.75

# Feature engineering

In [19]:
#diamonds_train_sorted['table_xy'] = (diamonds_train_sorted['table'].mean()*(diamonds_train_sorted['x']*diamonds_train_sorted['y']).mean()-diamonds_train_sorted['table']*(diamonds_train_sorted['x']*diamonds_train_sorted['y']))
#diamonds_train_sorted['depth_z'] = (diamonds_train_sorted['depth'].mean()*diamonds_train_sorted['z'].mean()-diamonds_train_sorted['depth']*diamonds_train_sorted['z'])
diamonds_train_sorted['volume'] = diamonds_train_sorted['x']*diamonds_train_sorted['y']*diamonds_train_sorted['z']
diamonds_train_sorted['super_feature'] = diamonds_train_sorted['carat'] / diamonds_train_sorted['table'] * diamonds_train_sorted['depth']
diamonds_train_sorted.head()

price  carat  cut  color  clarity  depth  table     x     y     z  \
0    326   0.21    4      1        2   59.8   61.0  3.89  3.84  2.31   
1    326   0.23    0      1        1   61.5   55.0  3.95  3.98  2.43   
2    327   0.23    1      1        4   56.9   65.0  4.05  4.07  2.31   
3    334   0.29    4      5        3   62.4   58.0  4.20  4.23  2.63   
4    335   0.31    1      6        1   63.3   58.0  4.34  4.35  2.75   

      table_xy   depth_z     volume  super_feature  
0  1046.867829  80.37688  34.505856       0.205869  
1  1093.406429  69.06988  38.202030       0.257182  
2   886.633929  87.07588  38.076885       0.201338  
3   927.633429  54.40288  46.724580       0.312000  
4   863.079429  44.43988  51.917250       0.338328

# Model train split

In [4]:
X = diamonds_train_sorted[['carat', 
                           'cut',
                           'color', 
                           'clarity',
                           'table_xy', 
                           'depth_z',
                          'volume',
                          'super_feature']]

y = diamonds_train_sorted['price']

In [5]:
# Train + test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)
print(f"X_train: {X_train.shape}, X_test: {X_test.shape}, y_train: {y_train.shape}, y_test: {y_test.shape}")
print(f"X_train: {type(X_train)}, X_test: {type(X_test)}, y_train: {type(y_train)}, y_test: {type(y_test)}")

X_train: (32344, 8), X_test: (8087, 8), y_train: (32344,), y_test: (8087,)
X_train: <class 'pandas.core.frame.DataFrame'>, X_test: <class 'pandas.core.frame.DataFrame'>, y_train: <class 'pandas.core.series.Series'>, y_test: <class 'pandas.core.series.Series'>


# Train model CatBoost

In [6]:
# rf model train
train_dataset = cb.Pool(X_train, y_train) 
test_dataset = cb.Pool(X_test, y_test)

In [7]:
model = cb.CatBoostRegressor(loss_function='RMSE')

In [8]:
grid = {'iterations': [100, 150, 500],
        'learning_rate': [0.03, 0.1, 0.3],
        'depth': [2, 4, 6, 8],
        'l2_leaf_reg': [0.2, 0.5, 1, 3]}
model.grid_search(grid, train_dataset)

0:	learn: 5454.4408061	test: 5503.2187478	best: 5503.2187478 (0)	total: 160ms	remaining: 15.9s
1:	learn: 5310.6307752	test: 5358.6344195	best: 5358.6344195 (1)	total: 163ms	remaining: 8.01s
2:	learn: 5170.0022869	test: 5218.4756087	best: 5218.4756087 (2)	total: 166ms	remaining: 5.36s
3:	learn: 5035.3521392	test: 5083.6634597	best: 5083.6634597 (3)	total: 168ms	remaining: 4.03s
4:	learn: 4904.6609609	test: 4953.0606505	best: 4953.0606505 (4)	total: 170ms	remaining: 3.23s
5:	learn: 4779.0929805	test: 4826.8148073	best: 4826.8148073 (5)	total: 172ms	remaining: 2.7s
6:	learn: 4655.8615146	test: 4703.4057762	best: 4703.4057762 (6)	total: 174ms	remaining: 2.31s
7:	learn: 4537.6100111	test: 4585.4311002	best: 4585.4311002 (7)	total: 176ms	remaining: 2.03s
8:	learn: 4427.9607799	test: 4475.5945519	best: 4475.5945519 (8)	total: 179ms	remaining: 1.81s
9:	learn: 4319.9032171	test: 4367.2486576	best: 4367.2486576 (9)	total: 181ms	remaining: 1.63s
10:	learn: 4212.0497590	test: 4259.4085638	best: 42

57:	learn: 990.3619540	test: 1062.1531610	best: 1062.1531610 (57)	total: 144ms	remaining: 104ms
58:	learn: 985.2460033	test: 1056.9045399	best: 1056.9045399 (58)	total: 146ms	remaining: 102ms
59:	learn: 980.8734447	test: 1052.5994931	best: 1052.5994931 (59)	total: 149ms	remaining: 99.1ms
60:	learn: 974.3914193	test: 1045.5204300	best: 1045.5204300 (60)	total: 151ms	remaining: 96.3ms
61:	learn: 966.8065940	test: 1037.3624040	best: 1037.3624040 (61)	total: 153ms	remaining: 94ms
62:	learn: 961.2676892	test: 1031.9604272	best: 1031.9604272 (62)	total: 156ms	remaining: 91.3ms
63:	learn: 955.8467494	test: 1025.7127143	best: 1025.7127143 (63)	total: 157ms	remaining: 88.6ms
64:	learn: 951.5921675	test: 1022.1616592	best: 1022.1616592 (64)	total: 160ms	remaining: 86ms
65:	learn: 944.6793788	test: 1014.3001426	best: 1014.3001426 (65)	total: 163ms	remaining: 83.7ms
66:	learn: 940.3074453	test: 1010.1168590	best: 1010.1168590 (66)	total: 165ms	remaining: 81.3ms
67:	learn: 934.9544821	test: 1003.89

50:	learn: 778.4051918	test: 835.2989683	best: 835.2989683 (50)	total: 104ms	remaining: 100ms
51:	learn: 776.4162442	test: 833.4300127	best: 833.4300127 (51)	total: 107ms	remaining: 98.3ms
52:	learn: 772.5327974	test: 829.9806143	best: 829.9806143 (52)	total: 109ms	remaining: 96.5ms
53:	learn: 768.6411896	test: 824.2935813	best: 824.2935813 (53)	total: 111ms	remaining: 94.4ms
54:	learn: 767.2252696	test: 823.2493198	best: 823.2493198 (54)	total: 114ms	remaining: 93.1ms
55:	learn: 763.9375957	test: 818.1947121	best: 818.1947121 (55)	total: 116ms	remaining: 91ms
56:	learn: 760.2280587	test: 815.5072019	best: 815.5072019 (56)	total: 118ms	remaining: 89.2ms
57:	learn: 758.8358404	test: 814.2335391	best: 814.2335391 (57)	total: 120ms	remaining: 87.1ms
58:	learn: 757.6999404	test: 813.0903932	best: 813.0903932 (58)	total: 122ms	remaining: 85ms
59:	learn: 756.9469200	test: 812.3396404	best: 812.3396404 (59)	total: 124ms	remaining: 82.8ms
60:	learn: 756.3030712	test: 809.2194588	best: 809.2194

37:	learn: 2356.3111436	test: 2413.4348418	best: 2413.4348418 (37)	total: 89ms	remaining: 145ms
38:	learn: 2315.1234496	test: 2372.9676216	best: 2372.9676216 (38)	total: 91.9ms	remaining: 144ms
39:	learn: 2275.5953577	test: 2334.2459015	best: 2334.2459015 (39)	total: 94.1ms	remaining: 141ms
40:	learn: 2238.1717958	test: 2297.6023646	best: 2297.6023646 (40)	total: 96.6ms	remaining: 139ms
41:	learn: 2202.3306864	test: 2262.1353862	best: 2262.1353862 (41)	total: 98.9ms	remaining: 137ms
42:	learn: 2168.0195550	test: 2228.0892023	best: 2228.0892023 (42)	total: 102ms	remaining: 135ms
43:	learn: 2135.6129803	test: 2196.2025332	best: 2196.2025332 (43)	total: 104ms	remaining: 132ms
44:	learn: 2103.6364771	test: 2164.6715320	best: 2164.6715320 (44)	total: 106ms	remaining: 130ms
45:	learn: 2073.1272589	test: 2134.6996954	best: 2134.6996954 (45)	total: 108ms	remaining: 127ms
46:	learn: 2042.9602321	test: 2105.4660996	best: 2105.4660996 (46)	total: 110ms	remaining: 125ms
47:	learn: 2013.5026634	tes

84:	learn: 871.3482621	test: 940.1294921	best: 940.1294921 (84)	total: 252ms	remaining: 44.4ms
85:	learn: 869.1185909	test: 937.9280926	best: 937.9280926 (85)	total: 255ms	remaining: 41.5ms
86:	learn: 865.6625357	test: 934.5891173	best: 934.5891173 (86)	total: 257ms	remaining: 38.4ms
87:	learn: 862.7337956	test: 930.7016831	best: 930.7016831 (87)	total: 260ms	remaining: 35.4ms
88:	learn: 860.7788826	test: 929.1807288	best: 929.1807288 (88)	total: 262ms	remaining: 32.4ms
89:	learn: 857.6455890	test: 925.9313402	best: 925.9313402 (89)	total: 266ms	remaining: 29.6ms
90:	learn: 855.1312542	test: 923.2449224	best: 923.2449224 (90)	total: 270ms	remaining: 26.7ms
91:	learn: 853.1145979	test: 921.6475180	best: 921.6475180 (91)	total: 273ms	remaining: 23.8ms
92:	learn: 851.4115193	test: 919.9403421	best: 919.9403421 (92)	total: 277ms	remaining: 20.9ms
93:	learn: 846.2759466	test: 912.9759984	best: 912.9759984 (93)	total: 282ms	remaining: 18ms
94:	learn: 843.0254804	test: 909.1043087	best: 909.1

...

160:	learn: 519.3974099	test: 580.6324804	best: 580.6324804 (160)	total: 744ms	remaining: 1.57s
161:	learn: 518.8704892	test: 579.9513313	best: 579.9513313 (161)	total: 749ms	remaining: 1.56s
162:	learn: 518.1937767	test: 579.7073149	best: 579.7073149 (162)	total: 753ms	remaining: 1.56s
163:	learn: 517.8465855	test: 579.3214647	best: 579.3214647 (163)	total: 757ms	remaining: 1.55s
164:	learn: 517.0278528	test: 578.9710644	best: 578.9710644 (164)	total: 761ms	remaining: 1.54s
165:	learn: 516.4416282	test: 578.8571787	best: 578.8571787 (165)	total: 767ms	remaining: 1.54s
166:	learn: 515.7537793	test: 579.0282596	best: 578.8571787 (165)	total: 772ms	remaining: 1.54s
167:	learn: 515.0611806	test: 578.5256767	best: 578.5256767 (167)	total: 776ms	remaining: 1.53s
168:	learn: 514.4531000	test: 578.1187811	best: 578.1187811 (168)	total: 781ms	remaining: 1.53s
169:	learn: 513.7818142	test: 578.2208367	best: 578.1187811 (168)	total: 785ms	remaining: 1.52s
170:	learn: 513.7395411	test: 578.142360

267:	learn: 481.4651946	test: 565.2057353	best: 565.2057353 (267)	total: 1.35s	remaining: 1.17s
268:	learn: 481.3402173	test: 565.2072794	best: 565.2057353 (267)	total: 1.36s	remaining: 1.17s
269:	learn: 481.1178000	test: 565.0808741	best: 565.0808741 (269)	total: 1.36s	remaining: 1.16s
270:	learn: 480.8889612	test: 564.8747192	best: 564.8747192 (270)	total: 1.36s	remaining: 1.15s
271:	learn: 480.6673038	test: 564.7401930	best: 564.7401930 (271)	total: 1.37s	remaining: 1.15s
272:	learn: 480.4569770	test: 564.7369939	best: 564.7369939 (272)	total: 1.38s	remaining: 1.14s
273:	learn: 480.2780977	test: 564.6063348	best: 564.6063348 (273)	total: 1.38s	remaining: 1.14s
274:	learn: 480.0991396	test: 564.4942298	best: 564.4942298 (274)	total: 1.39s	remaining: 1.13s
275:	learn: 480.0802202	test: 564.4505544	best: 564.4505544 (275)	total: 1.39s	remaining: 1.13s
276:	learn: 479.9416070	test: 564.4436452	best: 564.4436452 (276)	total: 1.4s	remaining: 1.13s
277:	learn: 479.4676607	test: 564.6055040

357:	learn: 459.6055219	test: 560.7596143	best: 560.6735617 (350)	total: 1.76s	remaining: 698ms
358:	learn: 459.3359485	test: 560.6458270	best: 560.6458270 (358)	total: 1.76s	remaining: 693ms
359:	learn: 459.1633328	test: 560.5802889	best: 560.5802889 (359)	total: 1.77s	remaining: 688ms
360:	learn: 458.9777216	test: 560.5128060	best: 560.5128060 (360)	total: 1.77s	remaining: 683ms
361:	learn: 458.8163027	test: 560.5812279	best: 560.5128060 (360)	total: 1.78s	remaining: 678ms
362:	learn: 458.7139078	test: 560.5361181	best: 560.5128060 (360)	total: 1.78s	remaining: 674ms
363:	learn: 458.5773024	test: 560.5123517	best: 560.5123517 (363)	total: 1.79s	remaining: 668ms
364:	learn: 458.5620257	test: 560.4832626	best: 560.4832626 (364)	total: 1.79s	remaining: 663ms
365:	learn: 458.3503787	test: 560.4870323	best: 560.4832626 (364)	total: 1.8s	remaining: 658ms
366:	learn: 458.1031951	test: 560.5283387	best: 560.4832626 (364)	total: 1.8s	remaining: 653ms
367:	learn: 458.0855819	test: 560.5314212	

447:	learn: 443.5785374	test: 558.7111238	best: 558.7111238 (447)	total: 2.17s	remaining: 251ms
448:	learn: 443.4785493	test: 558.6291559	best: 558.6291559 (448)	total: 2.17s	remaining: 247ms
449:	learn: 443.4063251	test: 558.5991832	best: 558.5991832 (449)	total: 2.17s	remaining: 242ms
450:	learn: 443.2489867	test: 558.5877905	best: 558.5877905 (450)	total: 2.18s	remaining: 237ms
451:	learn: 442.9173495	test: 558.5091069	best: 558.5091069 (451)	total: 2.18s	remaining: 232ms
452:	learn: 442.6661830	test: 558.4583771	best: 558.4583771 (452)	total: 2.19s	remaining: 227ms
453:	learn: 442.5198400	test: 558.4188299	best: 558.4188299 (453)	total: 2.19s	remaining: 222ms
454:	learn: 442.3118022	test: 558.3744014	best: 558.3744014 (454)	total: 2.2s	remaining: 217ms
455:	learn: 442.1513694	test: 558.3106547	best: 558.3106547 (455)	total: 2.2s	remaining: 212ms
456:	learn: 442.0439194	test: 558.2770330	best: 558.2770330 (456)	total: 2.21s	remaining: 208ms
457:	learn: 442.0242204	test: 558.2814472	

{'params': {'depth': 6,
  'l2_leaf_reg': 3,
  'iterations': 500,
  'learning_rate': 0.1},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               45,

# Predict model

In [20]:
# rf model predict
y_pred = model.predict(X_test)

# RMSE calculation

In [21]:
# RMSE calculation
rmse = mean_squared_error(y_test, y_pred, squared=False)
rmse

525.8703306587724

# Model train 100 %

In [29]:
model.fit(scaled_X, y)

In [23]:
"""
model = cb.CatBoostRegressor(loss_function='RMSE')
"""

In [37]:
"""
# rf model train
grid_b = {'iterations': [100, 150, 500],
        'learning_rate': [0.03, 0.1, 0.3],
        'depth': [2, 4, 6, 8],
        'l2_leaf_reg': [0.2, 0.5, 1, 3]}
model.grid_search(grid_b, train_dataset_100)
"""

"\n# rf model train\ngrid_b = {'iterations': [100, 150, 500],\n        'learning_rate': [0.03, 0.1, 0.3],\n        'depth': [2, 4, 6, 8],\n        'l2_leaf_reg': [0.2, 0.5, 1, 3]}\nmodel.grid_search(grid_b, train_dataset_100)\n"

# Read diamonds_test_processed

In [11]:
# Read diamonds_test_processed
diamonds_test_basic = pd.read_csv('../data/diamonds_test_processed.csv')
diamonds_test_basic.head()

carat  cut  color  clarity  depth  table     x     y     z
0   0.79    3      2        2   62.7   60.0  5.82  5.89  3.67
1   1.20    0      6        4   61.0   57.0  6.81  6.89  4.18
2   1.57    4      4        2   62.2   61.0  7.38  7.32  4.57
3   0.90    3      2        2   63.8   54.0  6.09  6.13  3.90
4   0.50    3      2        4   62.9   58.0  5.05  5.09  3.19

# Feature engineering

In [12]:
diamonds_test_basic['table_xy'] = (diamonds_test_basic['table'].mean()*(diamonds_test_basic['x']*diamonds_test_basic['y']).mean()-diamonds_test_basic['table']*(diamonds_test_basic['x']*diamonds_test_basic['y']))
diamonds_test_basic['depth_z'] = (diamonds_test_basic['depth'].mean()*diamonds_test_basic['z'].mean()-diamonds_test_basic['depth']*diamonds_test_basic['z'])
diamonds_test_basic['volume'] = diamonds_test_basic['x']*diamonds_test_basic['y']*diamonds_test_basic['z']
diamonds_test_basic['super_feature'] = diamonds_test_basic['carat'] / diamonds_test_basic['table'] * diamonds_test_basic['depth']
diamonds_test_basic.head()

carat  cut  color  clarity  depth  table     x     y     z    table_xy  \
0   0.79    3      2        2   62.7   60.0  5.82  5.89  3.67   -93.26473   
1   1.20    0      6        4   61.0   57.0  6.81  6.89  4.18  -710.96803   
2   1.57    4      4        2   62.2   61.0  7.38  7.32  4.57 -1331.79433   
3   0.90    3      2        2   63.8   54.0  6.09  6.13  3.90   -52.38853   
4   0.50    3      2        4   62.9   58.0  5.05  5.09  3.19   472.66227   

     depth_z      volume  super_feature  
0 -11.338107  125.806866       0.825550  
1 -36.209107  196.129362       1.284211  
2 -65.483107  246.878712       1.600885  
3 -30.049107  145.593630       1.063333  
4  18.119893   81.997355       0.542241

# Predict diamonds_test_basic

In [15]:
# Define fearures
X_dtfe_2 = diamonds_test_basic[['carat', 
                           'cut',
                           'color', 
                           'clarity',
                           'table_xy', 
                           'depth_z',
                          'volume',
                          'super_feature']]

In [16]:
# predict
y_predfe_2 = model.predict(X_dtfe_2).clip(0, 30000)
y_predfe_2 

array([2725.6395078 , 5689.81810138, 9829.4853736 , ..., 3211.48361798,
       2131.13999442,  761.05896198])

# Create sample_submission

In [17]:
predictions_fe_2 = pd.DataFrame(y_predfe_2).rename(columns = {0:'price'})
predictions_fe_2.index.names = ['id']
predictions_fe_2

price
id                
0      2725.639508
1      5689.818101
2      9829.485374
3      3870.563592
4      1586.696616
...            ...
13480  1638.572295
13481  2249.303920
13482  3211.483618
13483  2131.139994
13484   761.058962

[13485 rows x 1 columns]

In [18]:
predictions_fe_2.to_csv('../predictions/predictions_catboost.csv')